In [142]:
!pip install sklearn-genetic-opt
# Import necessary libraries
import pickle
import numpy as np
import pandas as pd
from scipy.signal import welch
from scipy.integrate import simps
from matplotlib import pyplot as plt
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression, Lasso
from sklearn.svm import SVC
from xgboost import XGBClassifier
from sklearn.model_selection import StratifiedKFold
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import accuracy_score, f1_score, precision_score, recall_score
from sklearn.feature_selection import SelectKBest, f_classif
from sklearn_genetic import GAFeatureSelectionCV, ExponentialAdapter

import time

/opt/conda/lib/python3.10/pty.py:89: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  pid, fd = os.forkpty()


In [143]:
# Function to read data
def read_data(filename):
    x = pickle._Unpickler(open(filename, 'rb'))
    x.encoding = 'latin1'
    data = x.load()
    return data

In [144]:
# Load data
files = [f"{i:02d}" for i in range(1, 23)]
labels = []
data = []
for i in files:
    fileph = "/kaggle/input/deap-dataset/data_preprocessed_python/s" + i + ".dat"
    d = read_data(fileph)
    labels.append(d['labels'])
    data.append(d['data'])

In [145]:
# Convert to numpy arrays
labels = np.array(labels)
data = np.array(data)

In [146]:
# Reshape data
labels = labels.reshape(880, 4)
data = data.reshape(880, 40, 8064)

In [147]:
# Extract EEG data
eeg_data = data[:, :32, :]

# Create labels dataframe
df_label = pd.DataFrame({'Valence': labels[:, 0], 'Arousal': labels[:, 1]})

In [148]:
# Describe and info
print(df_label.describe())
print(df_label.info())

# Binarize labels
labels_valence = (labels[:, 0] > 5).astype(int)
labels_arousal = (labels[:, 1] > 5).astype(int)
labels_dominance = (labels[:, 2] > 5).astype(int)
labels_liking = (labels[:, 3] > 6).astype(int)

          Valence     Arousal
count  880.000000  880.000000
mean     5.218034    5.238898
std      2.093837    1.879631
min      1.000000    1.000000
25%      3.650000    3.895000
50%      5.040000    5.490000
75%      7.040000    6.795000
max      9.000000    9.000000
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 880 entries, 0 to 879
Data columns (total 2 columns):
 #   Column   Non-Null Count  Dtype  
---  ------   --------------  -----  
 0   Valence  880 non-null    float64
 1   Arousal  880 non-null    float64
dtypes: float64(2)
memory usage: 13.9 KB
None


In [149]:
# Function to compute band power
def bandpower(data, sf, band):
    band = np.asarray(band)
    low, high = band
    nperseg = (2 / low) * sf
    freqs, psd = welch(data, sf, nperseg=nperseg)
    freq_res = freqs[1] - freqs[0]
    idx_band = np.logical_and(freqs >= low, freqs <= high)
    bp = simps(psd[idx_band], dx=freq_res)
    return bp

In [150]:
# Get band power
def get_band_power(people, channel, band):
    bands = {"delta": (0.5, 4), "theta": (4, 8), "alpha": (8, 12), "beta": (12, 30), "gamma": (30, 64)}
    return bandpower(eeg_data[people, channel], 128, bands[band])

eeg_band = []
for i in range(len(eeg_data)):
    for j in range(len(eeg_data[0])):
        eeg_band.extend([get_band_power(i, j, b) for b in ["delta", "theta", "alpha", "beta", "gamma"]])

eeg_band = np.array(eeg_band).reshape((880, 160))  # 5 bands x 32 channels
np.save("eeg_band.npy", eeg_band)
eeg_band = np.load("eeg_band.npy")

In [159]:
labels_combined = np.vstack((labels_valence, labels_arousal)).T
model_names = ['Logistic Regression', 'Random Forest', 'XGBoost', 'SVM']
models_lr = LogisticRegression(),
models_rf = RandomForestClassifier()
models_xgb = XGBClassifier(),
models_svc = SVC (kernel = 'linear')

In [152]:
# Function to compute metrics
def metrics(y_test, pred):
    accuracy = accuracy_score(y_test, pred)
    precision = precision_score(y_test, pred, average='macro')
    recall = recall_score(y_test, pred, average='macro')
    f1 = f1_score(y_test, pred, average='macro')
    return accuracy, precision, recall, f1

**without feature selection**

In [153]:
# Cross-validation and classification with feature selection
results = {name: {'accuracy': [], 'precision': [], 'recall': [], 'f1': [], 'time': []} for name in model_names}
cv = StratifiedKFold(n_splits=5, random_state=0, shuffle=True)
  # Adjust the number of features to select
def ML(model):
    print(model)
    # for model_name, model in zip(model_names, models_rf): 
    for label_type in range(2):  # For each label (valence, arousal, dominance, liking)
        X, y = eeg_band, labels_combined[:, label_type]
        scaler = StandardScaler()
        X = scaler.fit_transform(X)
        mean_acc = []
        mean_f1 = []
        for i, (train_index, test_index) in enumerate(cv.split(X, y)):
    #         print(f"{model_name} - Label {label_type} - Fold {i+1}")
            start_time = time.perf_counter()

            X_train, X_test = X_selected[train_index], X_selected[test_index]
            y_train, y_test = y[train_index], y[test_index]

            scaler = StandardScaler()
            X_train = scaler.fit_transform(X_train)
            X_test = scaler.transform(X_test)

            model.fit(X_train, y_train)
            pred = model.predict(X_test)
            accuracy, precision, recall, f1 = metrics(y_test, pred)
            mean_acc.append(accuracy)
            mean_f1.append(f1)
            results[model_name]['accuracy'].append(accuracy)
            results[model_name]['precision'].append(precision)
            results[model_name]['recall'].append(recall)
            results[model_name]['f1'].append(f1)

            elapsed_time = time.perf_counter() - start_time
            results[model_name]['time'].append(elapsed_time)
#             print(f"Time: {elapsed_time:.2f} seconds")
        if label_type == 0:
            print('Valence')
        else:
            print('Arousal')
        print('mean acc = ', np.mean(mean_acc))
        print('mean f1 = ', np.mean(mean_f1))
        print('mean time = ', np.mean(results[model_name]['time']))
# # Display results
# for model_name in model_names:
#     print(f"{model_name} Results:")
#     for metric in ['accuracy', 'precision', 'recall', 'f1', 'time']:
#         values = results[model_name][metric]
#         print(f"{metric.capitalize()}: Mean = {np.mean(values)* 100:.2f}, Std = {np.std(values):.4f}")


In [154]:
ML(LogisticRegression())
ML(RandomForestClassifier())  
ML(XGBClassifier())
ML(SVC(kernel = 'linear'))

LogisticRegression()


/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _c

Valence
mean acc =  0.6090909090909091
mean f1 =  0.6023485643573618
mean time =  0.05828264060000947


/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _c

Arousal
mean acc =  0.6318181818181818
mean f1 =  0.579008886850979
mean time =  0.05958879189984145
RandomForestClassifier()
Valence
mean acc =  0.6613636363636364
mean f1 =  0.6577856031194125
mean time =  0.2362856950664233
Arousal
mean acc =  0.6034090909090909
mean f1 =  0.580840830841667
mean time =  0.3269212621996303
XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=None, device=None, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=None, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=None, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              multi_strategy=None, n_estimat

**Filter-based feature selection method**


In [155]:
# Cross-validation and classification with feature selection
results = {name: {'accuracy': [], 'precision': [], 'recall': [], 'f1': [], 'time': []} for name in model_names}
cv = StratifiedKFold(n_splits=5, random_state=0, shuffle=True)
  # Adjust the number of features to select
def ML(model, selected_features):
    print(model)
    print('selected_features = ', selected_features)
    num_features_to_select = selected_features
    # for model_name, model in zip(model_names, models_rf): 
    for label_type in range(2):  # For each label (valence, arousal, dominance, liking)
        X, y = eeg_band, labels_combined[:, label_type]
        selector = SelectKBest(f_classif, k=num_features_to_select)
        X_selected = selector.fit_transform(X, y)
        scaler = StandardScaler()
        X_selected = scaler.fit_transform(X_selected)
        mean_acc = []
        mean_f1 = []
        for i, (train_index, test_index) in enumerate(cv.split(X_selected, y)):
    #         print(f"{model_name} - Label {label_type} - Fold {i+1}")
            start_time = time.perf_counter()

            X_train, X_test = X_selected[train_index], X_selected[test_index]
            y_train, y_test = y[train_index], y[test_index]

            scaler = StandardScaler()
            X_train = scaler.fit_transform(X_train)
            X_test = scaler.transform(X_test)

            model.fit(X_train, y_train)
            pred = model.predict(X_test)
            accuracy, precision, recall, f1 = metrics(y_test, pred)
            mean_acc.append(accuracy)
            mean_f1.append(f1)
            results[model_name]['accuracy'].append(accuracy)
            results[model_name]['precision'].append(precision)
            results[model_name]['recall'].append(recall)
            results[model_name]['f1'].append(f1)

            elapsed_time = time.perf_counter() - start_time
            results[model_name]['time'].append(elapsed_time)
#             print(f"Time: {elapsed_time:.2f} seconds")
        if label_type == 0:
            print('Valence')
        else:
            print('Arousal')
        print('mean acc = ', np.mean(mean_acc))
        print('mean f1 = ', np.mean(mean_f1))
        print('mean time = ', np.mean(results[model_name]['time']))
# # Display results
# for model_name in model_names:
#     print(f"{model_name} Results:")
#     for metric in ['accuracy', 'precision', 'recall', 'f1', 'time']:
#         values = results[model_name][metric]
#         print(f"{metric.capitalize()}: Mean = {np.mean(values)* 100:.2f}, Std = {np.std(values):.4f}")


In [156]:
ML(LogisticRegression(), 50)
ML(RandomForestClassifier(), 50)  
ML(XGBClassifier(), 50)
ML(SVC(kernel = 'linear'), 50)
ML(LogisticRegression(), 100)
ML(RandomForestClassifier(), 100)  
ML(XGBClassifier(), 100)
ML(SVC(kernel = 'linear'), 100)
ML(LogisticRegression(), 150)
ML(RandomForestClassifier(), 150)  
ML(XGBClassifier(), 150)
ML(SVC(kernel = 'linear'), 150)

LogisticRegression()
selected_features =  50


/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _c

Valence
mean acc =  0.5875
mean f1 =  0.5756988187348826
mean time =  0.07588789419969544


/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _c

Arousal
mean acc =  0.625
mean f1 =  0.5538706705407923
mean time =  0.06027676329977112
RandomForestClassifier()
selected_features =  50
Valence
mean acc =  0.6681818181818182
mean f1 =  0.6655865660114285
mean time =  0.2075870160000098
Arousal
mean acc =  0.6011363636363637
mean f1 =  0.5806674971519016
mean time =  0.27348564009989784
XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=None, device=None, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=None, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=None, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              multi_strategy=N

...

Arousal
mean acc =  0.6318181818181818
mean f1 =  0.579008886850979
mean time =  0.19495672719986032
RandomForestClassifier()
selected_features =  100
Valence
mean acc =  0.6602272727272728
mean f1 =  0.6562038717327885
mean time =  0.23183278809073354
Arousal
mean acc =  0.5897727272727273
mean f1 =  0.5696956164306688
mean time =  0.26107317049979123
XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=None, device=None, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=None, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=None, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              mu

/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _c

Valence
mean acc =  0.615909090909091
mean f1 =  0.6101501738666404
mean time =  0.2595072239998605


/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _c

Arousal
mean acc =  0.6454545454545455
mean f1 =  0.6013182034024069
mean time =  0.24870125052208703
RandomForestClassifier()
selected_features =  150
Valence
mean acc =  0.6465909090909092
mean f1 =  0.6426726041022043
mean time =  0.27125765382094724
Arousal
mean acc =  0.5977272727272728
mean f1 =  0.5750517926485404
mean time =  0.2902065513399248
XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=None, device=None, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=None, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=None, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              mu

**Embedded-based feature selection method**

In [166]:
from sklearn.model_selection import GridSearchCV
# Cross-validation and classification with feature selection
results = {name: {'accuracy': [], 'precision': [], 'recall': [], 'f1': [], 'time': []} for name in model_names}
cv = StratifiedKFold(n_splits=5, random_state=0, shuffle=True)


def ML(model):
    print(model)
    # for model_name, model in zip(model_names, models_rf): 
    for label_type in range(2):  # For each label (valence, arousal, dominance, liking)
        X, y = eeg_band, labels_combined[:, label_type]
        selected_features = []
        for label_index in range(labels_combined.shape[1]):
            y = labels_combined[:, label_index]
            lasso = Lasso()
            params = {'alpha': [0.0001, 0.001, 0.01, 0.1, 1, 10]}
            cv = StratifiedKFold(n_splits=5, random_state=0, shuffle=True)
            lasso_cv = GridSearchCV(lasso, param_grid=params, cv=cv)
            lasso_cv.fit(eeg_band, y)
            best_lasso = lasso_cv.best_estimator_
            lasso_coef = np.abs(best_lasso.coef_)
            selected_features.append(np.where(lasso_coef > 0.000001)[0])
        # Combine selected features for all labels
        selected_features = np.unique(np.concatenate(selected_features))
        print("Selected Feature: {}".format(len(selected_features)))
        X_selected = eeg_band[:, selected_features]
        scaler = StandardScaler()
        X_selected = scaler.fit_transform(X_selected)
        mean_acc = []
        mean_f1 = []
        for i, (train_index, test_index) in enumerate(cv.split(X_selected, y)):
    #         print(f"{model_name} - Label {label_type} - Fold {i+1}")
            start_time = time.perf_counter()

            X_train, X_test = X_selected[train_index], X_selected[test_index]
            y_train, y_test = y[train_index], y[test_index]

            scaler = StandardScaler()
            X_train = scaler.fit_transform(X_train)
            X_test = scaler.transform(X_test)

            model.fit(X_train, y_train)
            pred = model.predict(X_test)
            accuracy, precision, recall, f1 = metrics(y_test, pred)
            mean_acc.append(accuracy)
            mean_f1.append(f1)
            results[model_name]['accuracy'].append(accuracy)
            results[model_name]['precision'].append(precision)
            results[model_name]['recall'].append(recall)
            results[model_name]['f1'].append(f1)

            elapsed_time = time.perf_counter() - start_time
            results[model_name]['time'].append(elapsed_time)
#             print(f"Time: {elapsed_time:.2f} seconds")
        if label_type == 0:
            print('Valence')
        else:
            print('Arousal')
        print('mean acc = ', np.mean(mean_acc))
        print('mean f1 = ', np.mean(mean_f1))
        print('mean time = ', np.mean(results[model_name]['time']))
# # Display results
# for model_name in model_names:
#     print(f"{model_name} Results:")
#     for metric in ['accuracy', 'precision', 'recall', 'f1', 'time']:
#         values = results[model_name][metric]
#         print(f"{metric.capitalize()}: Mean = {np.mean(values)* 100:.2f}, Std = {np.std(values):.4f}")


In [167]:
ML(LogisticRegression())
ML(RandomForestClassifier())  
ML(XGBClassifier())
ML(SVC(kernel = 'linear'))

LogisticRegression()


/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 6.625e+01, tolerance: 1.752e-02
  model = cd_fast.enet_coordinate_descent(
/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 6.897e+01, tolerance: 1.751e-02
  model = cd_fast.enet_coordinate_descent(
/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 6.593e+01, tolerance: 1.751e

Selected Feature: 34


/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _c

Valence
mean acc =  0.6420454545454545
mean f1 =  0.5832062175228048
mean time =  0.06070971499975712


...

Selected Feature: 34
Arousal
mean acc =  0.5954545454545455
mean f1 =  0.5734584845235661
mean time =  0.2479471995668064
SVC(kernel='linear')


/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 6.625e+01, tolerance: 1.752e-02
  model = cd_fast.enet_coordinate_descent(
/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 6.897e+01, tolerance: 1.751e-02
  model = cd_fast.enet_coordinate_descent(
/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 6.593e+01, tolerance: 1.751e

Selected Feature: 34
Valence
mean acc =  0.6363636363636365
mean f1 =  0.5615470959030547
mean time =  0.22032261577156273


/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 6.625e+01, tolerance: 1.752e-02
  model = cd_fast.enet_coordinate_descent(
/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 6.897e+01, tolerance: 1.751e-02
  model = cd_fast.enet_coordinate_descent(
/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_coordinate_descent.py:631: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 6.593e+01, tolerance: 1.751e

Selected Feature: 34
Arousal
mean acc =  0.6363636363636365
mean f1 =  0.5615470959030547
mean time =  0.19922224400011146


**Wrapper-based feature selection method**

In [172]:
# Cross-validation and classification with feature selection
results = {name: {'accuracy': [], 'precision': [], 'recall': [], 'f1': [], 'time': []} for name in model_names}
cv = StratifiedKFold(n_splits=5, random_state=0, shuffle=True)


def ML(model):
    print(model)
    # for model_name, model in zip(model_names, models_rf): 
    for label_type in range(2):  # For each label (valence, arousal, dominance, liking)
        X, y = eeg_band, labels_combined[:, label_type]
        mutation_scheduler = ExponentialAdapter(0.8, 0.2, 0.01)
        crossover_scheduler = ExponentialAdapter(0.2, 0.8, 0.01)
        evolved_estimator = GAFeatureSelectionCV(
            estimator=model,
            scoring="accuracy",
            population_size=30,
            generations=20,
            mutation_probability=mutation_scheduler,
            crossover_probability=crossover_scheduler,
            n_jobs=-1,
            cv=5
        )
        
        evolved_estimator.fit(X, y)
        reduced_X = evolved_estimator.transform(X)
        print(f'Number of selected features for label: {reduced_X.shape[1]}')
        scaler = StandardScaler()
        X_selected = scaler.fit_transform(reduced_X)
        mean_acc = []
        mean_f1 = []
        for i, (train_index, test_index) in enumerate(cv.split(X_selected, y)):
    #         print(f"{model_name} - Label {label_type} - Fold {i+1}")
            start_time = time.perf_counter()

            X_train, X_test = X_selected[train_index], X_selected[test_index]
            y_train, y_test = y[train_index], y[test_index]

            scaler = StandardScaler()
            X_train = scaler.fit_transform(X_train)
            X_test = scaler.transform(X_test)

            model.fit(X_train, y_train)
            pred = model.predict(X_test)
            accuracy, precision, recall, f1 = metrics(y_test, pred)
            mean_acc.append(accuracy)
            mean_f1.append(f1)
            results[model_name]['accuracy'].append(accuracy)
            results[model_name]['precision'].append(precision)
            results[model_name]['recall'].append(recall)
            results[model_name]['f1'].append(f1)

            elapsed_time = time.perf_counter() - start_time
            results[model_name]['time'].append(elapsed_time)
#             print(f"Time: {elapsed_time:.2f} seconds")
        if label_type == 0:
            print('Valence')
        else:
            print('Arousal')
        print('mean acc = ', np.mean(mean_acc))
        print('mean f1 = ', np.mean(mean_f1))
        print('mean time = ', np.mean(results[model_name]['time']))
# # Display results
# for model_name in model_names:
#     print(f"{model_name} Results:")
#     for metric in ['accuracy', 'precision', 'recall', 'f1', 'time']:
#         values = results[model_name][metric]
#         print(f"{metric.capitalize()}: Mean = {np.mean(values)* 100:.2f}, Std = {np.std(values):.4f}")


In [ ]:
ML(LogisticRegression())
ML(RandomForestClassifier())  
ML(XGBClassifier())
ML(SVC(kernel = 'linear'))

LogisticRegression()


/opt/conda/lib/python3.10/site-packages/deap/creator.py:185: RuntimeWarning: A class named 'FitnessMax' has already been created and it will be overwritten. Consider deleting previous creation of that class or rename it.
  warnings.warn("A class named '{0}' has already been created and it "
/opt/conda/lib/python3.10/site-packages/deap/creator.py:185: RuntimeWarning: A class named 'Individual' has already been created and it will be overwritten. Consider deleting previous creation of that class or rename it.
  warnings.warn("A class named '{0}' has already been created and it "
/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn

gen	nevals	fitness 	fitness_std	fitness_max	fitness_min
0  	30    	0.464205	0.0161074  	0.505682   	0.431818   


/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _c

1  	60    	0.483674	0.0132017  	0.509091   	0.459091   


...

20 	60    	0.399167	0.0153751  	0.418182   	0.365909   


/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _c

Number of selected features for label: 85


/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _c

Arousal
mean acc =  0.6363636363636364
mean f1 =  0.5812802794209097
mean time =  0.055962055999953006
RandomForestClassifier()
gen	nevals	fitness 	fitness_std	fitness_max	fitness_min
0  	30    	0.477652	0.0128509  	0.506818   	0.457955   
1  	60    	0.494583	0.0082868  	0.506818   	0.476136   
2  	60    	0.499053	0.00732394 	0.509091   	0.478409   
3  	60    	0.49928 	0.00886793 	0.515909   	0.471591   
4  	60    	0.501098	0.0112551  	0.515909   	0.470455   
5  	60    	0.502614	0.0099722  	0.515909   	0.479545   
6  	60    	0.504394	0.0105616  	0.515909   	0.481818   
7  	60    	0.503561	0.0121781  	0.515909   	0.470455   
8  	60    	0.503295	0.0121944  	0.515909   	0.476136   
9  	60    	0.502311	0.0114447  	0.515909   	0.479545   
10 	60    	0.503106	0.0110718  	0.515909   	0.479545   
11 	60    	0.501932	0.0108567  	0.518182   	0.479545   
12 	60    	0.503295	0.0107899  	0.515909   	0.485227   
13 	60    	0.499508	0.0120322  	0.515909   	0.477273   
14 	60    	0.501212	0.0114614  	